# The main target of this notebook is diplay the real location of fires of last 24 hours in the brazilian amazon using satelit data from the brazilian research space agency (INPE) API.

### 1st Target

    Request data from INPE as json file

More information at: https://queimadas.dgi.inpe.br/queimadas/dados-abertos

Countries IDs

[ { "pais_id": 68, "pais_name": "Ecuador" }, { "pais_id": 245, "pais_name": "Uruguay" }, { "pais_id": 12, "pais_name": "Argentina" }, { "pais_id": 28, "pais_name": "Bolivia" }, { "pais_id": 75, "pais_name": "Falkland Islands" }, { "pais_id": 80, "pais_name": "French Guiana" }, { "pais_id": 98, "pais_name": "Guyana" }, { "pais_id": 33, "pais_name": "Brasil" }, { "pais_id": 48, "pais_name": "Chile" }, { "pais_id": 53, "pais_name": "Colombia" }, { "pais_id": 249, "pais_name": "Venezuela" }, { "pais_id": 177, "pais_name": "Paraguay" }, { "pais_id": 178, "pais_name": "Peru" }, { "pais_id": 219, "pais_name": "Suriname" } ]

In [1]:
##importing libs

import json
import requests
import pandas as pd
import folium

In [ ]:
def getINPE_totalFire(countryID = None, stateID = None, cityID = None, satelliteName = None):
  base_url = 'https://queimadas.dgi.inpe.br/queimadas/dados-abertos/api/focos/count'
  params_dict = {'pais_id' : countryID, 'estado_id' : stateID, 'municipio_id' : cityID, 'satelite' : satelliteName}
  resp = requests.get(base_url, params = params_dict)
  return resp.url, resp.json(), resp.headers['Date']
  

In [ ]:
def getINPE_location(countryID = None, stateID = None, cityID = None, satelliteName = None):
  base_url = 'https://queimadas.dgi.inpe.br/queimadas/dados-abertos/api/focos/'
  params_dict = {'pais_id' : countryID, 'estado_id' : stateID, 'municipio_id' : cityID, 'satelite' : satelliteName}
  resp = requests.get(base_url, params = params_dict)
  return resp.url, resp.json(), resp.headers['Date']

Save json file for offline investigation

In [ ]:
#with open('/data/TotalFires_Offline.txt', 'w') as outfile:
#  outfile.write(json.dumps(fire_counts, indent=2))

In [ ]:
#with open('/data/FiresLocation_Offline.txt', 'w') as outfile:
#  outfile.write(json.dumps(fire_location, indent=2))

Read json file for offline investigation

In [2]:
with open('data/FiresLocation_Offline.txt', 'r') as infile:
  offlineFires = json.loads(infile.read())

In [3]:
offlineFires

['https://queimadas.dgi.inpe.br/queimadas/dados-abertos/api/focos/',
 [{'geometry': {'type': 'Point', 'coordinates': [-62.78, 8.64]},
   'properties': {'risco_fogo': None,
    'longitude': -62.78,
    'data_hora_gmt': '2021-05-16T03:36:27+00:00',
    'precipitacao': None,
    'latitude': 8.64,
    'pais': 'Venezuela',
    'numero_dias_sem_chuva': None,
    'estado': 'Monagas',
    'municipio': 'Libertador',
    'satelite': 'GOES-16'},
   'type': 'Feature',
   'id': 'focos_ams_24h.392a39b0-af7c-34dd-a7a1-53ca318dfc53',
   'geometry_name': 'geom'},
  {'geometry': {'type': 'Point', 'coordinates': [-60.98, -21.67]},
   'properties': {'risco_fogo': None,
    'longitude': -60.98,
    'data_hora_gmt': '2021-05-16T03:33:10+00:00',
    'precipitacao': None,
    'latitude': -21.67,
    'pais': 'Paraguay',
    'numero_dias_sem_chuva': None,
    'estado': 'Boquerón',
    'municipio': 'General Eugenio A. Garay',
    'satelite': 'GOES-16'},
   'type': 'Feature',
   'id': 'focos_ams_24h.ef4f6e91-3bda

In [4]:
with open('data/FiresLocation_Offline.json', 'r') as infile:
  offlineFiresJSON = json.loads(infile.read())

In [5]:
# Normalizing data

df = pd.json_normalize(offlineFiresJSON[1])

In [6]:
df

type                                                 id  \
0     Feature  focos_ams_24h.392a39b0-af7c-34dd-a7a1-53ca318d...   
1     Feature  focos_ams_24h.ef4f6e91-3bda-31c0-9480-f364348b...   
2     Feature  focos_ams_24h.9de8dc23-1e78-34da-8a43-44687943...   
3     Feature  focos_ams_24h.805f7127-79f9-303c-86a5-8f731e30...   
4     Feature  focos_ams_24h.cb0a359c-3f92-356b-98e8-5735c06b...   
...       ...                                                ...   
5640  Feature  focos_ams_24h.04ba883d-efa7-3bff-95a6-c5ed6a03...   
5641  Feature  focos_ams_24h.01bfebd0-24a7-3da8-b5a3-1b434dfc...   
5642  Feature  focos_ams_24h.e66cb49b-3a93-3a5d-9e4b-020419c4...   
5643  Feature  focos_ams_24h.c925b781-d883-3e79-a50d-aac99bf3...   
5644  Feature  focos_ams_24h.186861ac-7971-3e07-bb1c-17624d33...   

     geometry_name geometry.type geometry.coordinates properties.risco_fogo  \
0             geom         Point       [-62.78, 8.64]                  None   
1             geom         Point     [-60.98, -21.67]                  None   
2             geom         Point     [-60.98, -21.69]                  None   
3             geom         Point       [-63.62, 9.64]                  None   
4             geom         Point       [-62.78, 8.64]                  None   
...            ...           ...                  ...                   ...   
5640          geom         Point   [-52.978, -19.876]                  None   
5641          geom         Point   [-53.014, -19.868]                  None   
5642          geom         Point       [-63.62, 9.64]                  None   
5643          geom         Point       [-63.55, 9.62]                  None   
5644          geom         Point       [-62.73, 8.94]                  None   

      properties.longitude   properties.data_hora_gmt properties.precipitacao  \
0                  -62.780  2021-05-16T03:36:27+00:00                    None   
1                  -60.980  2021-05-16T03:33:10+00:00                    None   
2                  -60.980  2021-05-16T03:33:09+00:00                    None   
3                  -63.620  2021-05-16T03:26:33+00:00                    None   
4                  -62.780  2021-05-16T03:26:27+00:00                    None   
...                    ...                        ...                     ...   
5640               -52.978  2021-05-15T04:10:00+00:00                    None   
5641               -53.014  2021-05-15T04:10:00+00:00                    None   
5642               -63.620  2021-05-15T04:06:33+00:00                    None   
5643               -63.550  2021-05-15T04:06:33+00:00                    None   
5644               -62.730  2021-05-15T04:06:29+00:00                    None   

      properties.latitude properties.pais properties.numero_dias_sem_chuva  \
0                   8.640       Venezuela                             None   
1                 -21.670        Paraguay                             None   
2                 -21.690        Paraguay                             None   
3                   9.640       Venezuela                             None   
4                   8.640       Venezuela                             None   
...                   ...             ...                              ...   
5640              -19.876          Brasil                             None   
5641              -19.868          Brasil                             None   
5642                9.640       Venezuela                             None   
5643                9.620       Venezuela                             None   
5644                8.940       Venezuela                             None   

       properties.estado      properties.municipio properties.satelite  
0                Monagas                Libertador             GOES-16  
1               Boquerón  General Eugenio A. Garay             GOES-16  
2               Boquerón  General Eugenio A. Garay             GOES-16  
3                Monagas             Sant

In [7]:
df.keys()

Index(['type', 'id', 'geometry_name', 'geometry.type', 'geometry.coordinates',
       'properties.risco_fogo', 'properties.longitude',
       'properties.data_hora_gmt', 'properties.precipitacao',
       'properties.latitude', 'properties.pais',
       'properties.numero_dias_sem_chuva', 'properties.estado',
       'properties.municipio', 'properties.satelite'],
      dtype='object')

In [91]:
df['properties.pais'].value_counts()

Brasil       1978
Bolivia      1273
Venezuela     583
Paraguay      562
Argentina     534
Colombia      371
Chile         272
Peru           29
Uruguay        19
Ecuador        14
Guyana         10
Name: properties.pais, dtype: int64

In [92]:
df['properties.satelite'].value_counts()

GOES-16      1803
NPP-375      1719
NOAA-20      1463
AQUA_M-T      225
TERRA_M-T     210
METOP-B        90
NOAA-18D       84
AQUA_M-M       37
MSG-03         11
NOAA-19         2
TERRA_M-M       1
Name: properties.satelite, dtype: int64

In [35]:
condition = df['properties.pais'] == "Brasil"

df_BR = df[condition]

In [36]:
df_BR

type                                                 id  \
22    Feature  focos_ams_24h.4eafffa8-0308-3225-922e-67aef42e...   
23    Feature  focos_ams_24h.aadd371e-380d-3b48-83aa-a134ae76...   
29    Feature  focos_ams_24h.8e43bcc3-1a41-3eec-8b99-4f33a0ba...   
30    Feature  focos_ams_24h.e1b6b5b4-13e0-3d09-a6d2-519d5d3d...   
36    Feature  focos_ams_24h.b0d1b986-d717-3fb6-9436-61207f9d...   
...       ...                                                ...   
5637  Feature  focos_ams_24h.c97d4053-3370-33ce-8254-28eb45bc...   
5638  Feature  focos_ams_24h.71eeb574-f5ef-3bee-af28-75325575...   
5639  Feature  focos_ams_24h.c6eed05f-27e7-3f8f-9ffc-1576d1e9...   
5640  Feature  focos_ams_24h.04ba883d-efa7-3bff-95a6-c5ed6a03...   
5641  Feature  focos_ams_24h.01bfebd0-24a7-3da8-b5a3-1b434dfc...   

     geometry_name geometry.type geometry.coordinates properties.risco_fogo  \
22            geom         Point     [-45.18, -20.68]                  None   
23            geom         Point     [-45.18, -20.66]                  None   
29            geom         Point     [-45.18, -20.68]                  None   
30            geom         Point     [-45.18, -20.66]                  None   
36            geom         Point     [-45.18, -20.68]                  None   
...            ...           ...                  ...                   ...   
5637          geom         Point   [-49.289, -20.577]                  None   
5638          geom         Point   [-49.309, -20.574]                  None   
5639          geom         Point   [-52.986, -19.878]                  None   
5640          geom         Point   [-52.978, -19.876]                  None   
5641          geom         Point   [-53.014, -19.868]                  None   

      properties.longitude   properties.data_hora_gmt properties.precipitacao  \
22                 -45.180  2021-05-16T02:53:17+00:00                    None   
23                 -45.180  2021-05-16T02:53:17+00:00                    None   
29                 -45.180  2021-05-16T02:43:18+00:00                    None   
30                 -45.180  2021-05-16T02:43:18+00:00                    None   
36                 -45.180  2021-05-16T02:33:18+00:00                    None   
...                    ...                        ...                     ...   
5637               -49.289  2021-05-15T04:10:00+00:00                    None   
5638               -49.309  2021-05-15T04:10:00+00:00                    None   
5639               -52.986  2021-05-15T04:10:00+00:00                    None   
5640               -52.978  2021-05-15T04:10:00+00:00                    None   
5641               -53.014  2021-05-15T04:10:00+00:00                    None   

      properties.latitude properties.pais properties.numero_dias_sem_chuva  \
22                -20.680          Brasil                             None   
23                -20.660          Brasil                             None   
29                -20.680          Brasil                             None   
30                -20.660          Brasil                             None   
36                -20.680          Brasil                             None   
...                   ...             ...                              ...   
5637              -20.577          Brasil                             None   
5638              -20.574          Brasil                             None   
5639              -19.878          Brasil                             None   
5640              -19.876          Brasil                             None   
5641              -19.868          Brasil                             None   

       properties.estado properties.municipio properties.satelite  
22          MINAS GERAIS             CANDEIAS             GOES-16  
23          MINAS GERAIS              CAMACHO             GOES-16  
29          MINAS GERAIS             CANDEIAS             GOES-16  
30          MINAS GERAIS              CAMACHO             GOE

In [37]:
latitude_mean = df_BR['properties.latitude'].mean()

In [38]:
longitude_mean = df_BR['properties.longitude'].mean()

In [115]:
map = folium.Map(location=[latitude_mean, longitude_mean], width=750, height=500, control_scale=True)

In [116]:
map

In [117]:
for latitude, longitude in df_BR['geometry.coordinates']:
    coordinates_msg = "coordinates: [{},{}]\n".format(longitude, latitude)
    folium.Marker([longitude, latitude], popup=coordinates_msg).add_to(map)

In [118]:
for i in range(len(df_BR)): 
    mesage = ("Coordinates: "+ str(df_BR.iloc[i,4]) + '<br>' + "Country: " + str(df_BR.iloc[i,10]) + '<br>' 
          + "State: " + str(df_BR.iloc[i,12]) + '<br>' + "City: " + str(df_BR.iloc[i,13])
          + '<br>' + "Satellite: " + str(df_BR.iloc[i,14]))
    popup = folium.Popup(mesage, min_width=300, max_width=300)
    folium.Marker([df_BR.iloc[i,9],df_BR.iloc[i,6]], popup=popup).add_to(map)
         

In [119]:
map

In [120]:
map2 = folium.Map(location=[latitude_mean, longitude_mean], width=750, height=500, control_scale=True)

for i in range(len(df_BR)): 
    mesage = ("Coordinates: "+ str(df_BR.iloc[i,4]) + '<br>' + "Country: " + str(df_BR.iloc[i,10]) + '<br>' 
          + "State: " + str(df_BR.iloc[i,12]) + '<br>' + "City: " + str(df_BR.iloc[i,13])
          + '<br>' + "Satellite: " + str(df_BR.iloc[i,14]))
    popup = folium.Popup(mesage, min_width=300, max_width=300)
    folium.Marker([df_BR.iloc[i,9],df_BR.iloc[i,6]], popup=popup, icon=folium.Icon(color='lightred', prefix='fa', icon='fa-solid fa-fire')).add_to(map2)
         

In [121]:
map2

In [151]:
map3 = folium.Map(location = [-15,-60], tiles='Cartodb dark_matter', zoom_start = 4)

#heat_data = [[point.xy[1][0], point.xy[0][0]] for point in df['geometry.coordinates']


points_inverse = []
for point in df_BR['geometry.coordinates']:
    points_inverse.append(point)
    
heat_data = []

for lng, lat in points_inverse:
    coordinate = [lat, lng]
    heat_data.append(coordinate)
          
          
#heat_data
#plugins.HeatMap(heat_data).add_to(map)

In [152]:
points_inverse

[[-45.18, -20.68],
 [-45.18, -20.66],
 [-45.18, -20.68],
 [-45.18, -20.66],
 [-45.18, -20.68],
 [-45.18, -20.66],
 [-45.18, -20.68],
 [-45.18, -20.66],
 [-52.76, -11.94],
 [-49.6582, -8.9427],
 [-52.7583, -11.897],
 [-52.7695, -11.8991],
 [-52.7609, -11.8873],
 [-52.772, -11.8894],
 [-56.7938, -16.295],
 [-56.8012, -16.2962],
 [-50.466, -16.5827],
 [-50.4791, -16.5854],
 [-55.0896, -18.4779],
 [-55.0973, -18.4792],
 [-56.0011, -21.2741],
 [-56.0087, -21.2754],
 [-54.1959, -21.2567],
 [-52.76, -11.94],
 [-49.2994, -20.54],
 [-49.3023, -20.5304],
 [-49.67, -9.02],
 [-49.6794, -8.979],
 [-49.6818, -8.9693],
 [-49.67, -9.02],
 [-52.7675, -11.9055],
 [-52.7768, -11.9078],
 [-52.7861, -11.91],
 [-52.7699, -11.8958],
 [-52.7792, -11.8981],
 [-54.4461, -12.3338],
 [-53.7563, -14.5587],
 [-56.8013, -16.2674],
 [-56.8085, -16.269],
 [-50.4869, -16.5846],
 [-50.4786, -16.5722],
 [-50.4895, -16.5749],
 [-55.0959, -18.4557],
 [-55.1031, -18.4573],
 [-55.1103, -18.4589],
 [-55.0982, -18.4459],
 [-51

In [153]:
heat_data

[[-20.68, -45.18],
 [-20.66, -45.18],
 [-20.68, -45.18],
 [-20.66, -45.18],
 [-20.68, -45.18],
 [-20.66, -45.18],
 [-20.68, -45.18],
 [-20.66, -45.18],
 [-11.94, -52.76],
 [-8.9427, -49.6582],
 [-11.897, -52.7583],
 [-11.8991, -52.7695],
 [-11.8873, -52.7609],
 [-11.8894, -52.772],
 [-16.295, -56.7938],
 [-16.2962, -56.8012],
 [-16.5827, -50.466],
 [-16.5854, -50.4791],
 [-18.4779, -55.0896],
 [-18.4792, -55.0973],
 [-21.2741, -56.0011],
 [-21.2754, -56.0087],
 [-21.2567, -54.1959],
 [-11.94, -52.76],
 [-20.54, -49.2994],
 [-20.5304, -49.3023],
 [-9.02, -49.67],
 [-8.979, -49.6794],
 [-8.9693, -49.6818],
 [-9.02, -49.67],
 [-11.9055, -52.7675],
 [-11.9078, -52.7768],
 [-11.91, -52.7861],
 [-11.8958, -52.7699],
 [-11.8981, -52.7792],
 [-12.3338, -54.4461],
 [-14.5587, -53.7563],
 [-16.2674, -56.8013],
 [-16.269, -56.8085],
 [-16.5846, -50.4869],
 [-16.5722, -50.4786],
 [-16.5749, -50.4895],
 [-18.4557, -55.0959],
 [-18.4573, -55.1031],
 [-18.4589, -55.1103],
 [-18.4459, -55.0982],
 [-17

In [154]:

from folium import plugins

plugins.HeatMap(heat_data).add_to(map3)

In [155]:
map3